In [ ]:
from datasets import load_dataset

In [ ]:
ds = load_dataset("csv", data_files="https://zenodo.org/record/3257041/files/xml2csv_alto.csv?download=1")

In [ ]:
def parse_wc(example):
    if wc := example['wc']:
        wc = wc.split(" ")
        wc = [float(x) for x in wc]
        return wc
    else:
        return []

In [ ]:
ds = ds.map(lambda x: {"wc":parse_wc(x)},num_proc=4, writer_batch_size=3000)

In [ ]:
!wget -O corpus-language.pkl https://zenodo.org/record/3257041/files/corpus-language.pkl?download=1

In [ ]:
import pickle

In [ ]:
with open("corpus-language.pkl","rb") as f:
    data = pickle.load(f)

In [ ]:
data

In [ ]:
data['in'] = data['ppn'] + "_" + data['filename']

In [ ]:
data = data.drop_duplicates(subset=['in'])

In [ ]:
data = data.set_index("in")

In [ ]:
data

In [ ]:
lookup_dict = data.to_dict('index')

In [ ]:
def lookup_lang_confidence(example):
    ppn = example['ppn']
    fname = example['file name']
    if match := lookup_dict.get(f"PPN{ppn}_{fname}"):
        return {"language": match['language'],'language_confidence': match['confidence']}
    else:
        return {"language": None,"language_confidence": None}

In [ ]:
lookup_lang_confidence(ds['train'][1])

In [ ]:
ds = ds.map(lambda x:lookup_lang_confidence(x))

In [ ]:
ds.push_to_hub('biglam/berlin_state_library_ocr')